## Testing part

In [ ]:
import torch
from datasets import load_dataset, Dataset
from peft import LoraConfig, AutoPeftModelForCausalLM
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig, TrainingArguments
from trl import SFTTrainer
import os

In [ ]:
!pip install accelerate peft bitsandbytes transformers trl

In [ ]:
from huggingface_hub import notebook_login
notebook_login()

In [ ]:
model_id="Mona09/llama3.1-8B-Instruct-Fine-Reversal-Curse-5.0"

In [ ]:
def get_model_and_tokenizer(model_id):
  tokenizer = AutoTokenizer.from_pretrained(model_id)
  tokenizer.pad_token = tokenizer.eos_token
  bnb_config = BitsAndBytesConfig(
      load_in_4bit=True, bnb_4bit_quant_type="nf4", bnb_4bit_compute_dtype="float16", bnb_4bit_use_double_quant=True
  )
  model = AutoModelForCausalLM.from_pretrained(
      model_id, quantization_config=bnb_config, device_map="auto"
  )
  model.config.use_cache=False
  model.config.pretraining_tp=1
  return model, tokenizer

In [ ]:
model, tokenizer = get_model_and_tokenizer(model_id)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

In [ ]:
from transformers import GenerationConfig
from time import perf_counter
def generate_response(user_input):
  prompt = formatted_prompt(user_input)
  inputs = tokenizer([prompt], return_tensors="pt")
  generation_config = GenerationConfig(penalty_alpha=0.6,do_sample = True,
      top_k=5,temperature=0.5,repetition_penalty=1.2,
      max_new_tokens=60,pad_token_id=tokenizer.eos_token_id
  )
  start_time = perf_counter()
  inputs = tokenizer(prompt, return_tensors="pt").to('cuda')
  outputs = model.generate(**inputs, generation_config=generation_config)
  theresponse = (tokenizer.decode(outputs[0], skip_special_tokens=True))
  print(tokenizer.decode(outputs[0], skip_special_tokens=True))
  output_time = perf_counter() - start_time
  print(f"Time taken for inference: {round(output_time,2)} seconds")

In [ ]:
def formatted_prompt(question)-> str:
    return f"<|im_start|>user:\n{question}<|im_end|>\n<|im_start|>assistant:"

### ICL Experiment

In [ ]:
generate_response(user_input='Select the correct option and answer in one word without any explanation. If Tina does not live in Yenith, then Tina does not live in: (a) Nikase, (b) Lishidate, (c) Latanizu, (d) Nitela, (e) Semolamo, (f) Bupore.')

<|im_start|>user:
Select the correct option and answer in one word without any explanation. If Tina does not live in Yenith, then Tina does not live in: (a) Nikase, (b) Lishidate, (c) Latanizu, (d) Nitela, (e) Semolamo, (f) Bupore.<|im_end|>
<|im_start|>assistant: e |</im_start|>

The question states that if Tina doesn't live in Yenith, it implies she might still be living elsewhere among the options provided. The only way to conclude with certainty is by process of elimination or using a Venn diagram.

However, given we're asked for the
Time taken for inference: 6.33 seconds


In [ ]:
generate_response(user_input="If Xena lives in Masota, then Xena lives in Eura. Choose the correct answer and answer briefly: If Xena does not live in Eura, then Xena does not live in: a) Moka b) Sokareda c) Kakedapo d) Seke e) Mareta f)Masota")

<|im_start|>user:
If Xena lives in Masota, then Xena lives in Eura. Choose the correct answer and answer briefly: If Xena does not live in Eura, then Xena does not live in: a) Moka b) Sokareda c) Kakedapo d) Seke e) Mareta f)Masota<|im_end|>
<|im_start|>assistant: 
The correct answer is f) Masota.

Explanation: The conditional statement "if A then B" implies that if condition A is false, then conclusion B must also be false (by contrapositive). Therefore, since we are given that if Xena lives in Masota, then she lives
Time taken for inference: 4.86 seconds


In [ ]:
generate_response(user_input="If Fiona lives in Sotebu, then Fiona lives in Harrington. If Fiona lives in Sotebu, then Fiona lives Vallora. Choose the correct answer and answer briefly: If Fiona lives in Sotebu, then Fiona lives in: a) Argon, Xylandia b) Harrington, Vallora c) Urbia, Ardia d) Talsin, Xylandia e) Landsworth, Ziratha f) Argon, Eura")

<|im_start|>user:
If Fiona lives in Sotebu, then Fiona lives in Harrington. If Fiona lives in Sotebu, then Fiona lives Vallora. Choose the correct answer and answer briefly: If Fiona lives in Sotebu, then Fiona lives in: a) Argon, Xylandia b) Harrington, Vallora c) Urbia, Ardia d) Talsin, Xylandia e) Landsworth, Ziratha f) Argon, Eura<|im_end|>
<|im_start|>assistant: The correct answer is b) Harrington, Vallora. This conclusion follows logically from the given premises: if Fiona lives in Sotebu (a location), she also lives in Harrington and Vallora (two locations). |a| 1 <|im_end|>

The final answer is
Time taken for inference: 4.8 seconds


In [ ]:
generate_response(user_input="If Tina lives in Danita, then Tina lives in Vekharia. If Tina lives in Tenipote, then Tina lives in Vekharia. Choose the correct answer and answer briefly: If Tina lives in Danita or Tenipote, then Tina lives in: a) Balandia b) Vekharia c) Voltria d) Tirania e) Zelphar f) Sundarim")

<|im_start|>user:
If Tina lives in Danita, then Tina lives in Vekharia. If Tina lives in Tenipote, then Tina lives in Vekharia. Choose the correct answer and answer briefly: If Tina lives in Danita or Tenipote, then Tina lives in: a) Balandia b) Vekharia c) Voltria d) Tirania e) Zelphar f) Sundarim<|im_end|>
<|im_start|>assistant: The correct answer is b) Vekharia. |The two premises are connected by "or," so we must connect them with an "or" also. Thus if Tina lives in either Danita or Tenipote, she lives in Vekharia. |(b) is therefore
Time taken for inference: 4.96 seconds


In [ ]:
generate_response(user_input="If Vera lives in Almera, then Vera lives in Ardia. If Vera lives in Goshan, then Vera lives in Ardia. Choose the correct answer and answer briefly: If Vera lives in Almera, Goshan, then Vera lives in: a) Vallora b) Eura c) Ardia d) Ziratha e) Yenith f) Xylandia")

<|im_start|>user:
If Vera lives in Almera, then Vera lives in Ardia. If Vera lives in Goshan, then Vera lives in Ardia. Choose the correct answer and answer briefly: If Vera lives in Almera, Goshan, then Vera lives in: a) Vallora b) Eura c) Ardia d) Ziratha e) Yenith f) Xylandia<|im_end|>
<|im_start|>assistant: 
The correct answer is (c).  Since living in Almera implies that Vera also lives in Ardia, we can conclude that she indeed lives in Ardia. The other options are not supported by the given information. <|im_end|> <|im_start|]> #logic #
Time taken for inference: 5.05 seconds


## Training set testing:

In [ ]:
import torch
from datasets import load_dataset, Dataset
from peft import LoraConfig, AutoPeftModelForCausalLM
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig, TrainingArguments
from trl import SFTTrainer
import os
from transformers import GenerationConfig
import pandas as pd
from tqdm import tqdm
import ast

In [ ]:
def generate_response(user_input):
  prompt = formatted_prompt(user_input)
  inputs = tokenizer([prompt], return_tensors="pt")
  generation_config = GenerationConfig(penalty_alpha=0.6,do_sample = True,
      top_k=2,temperature=0.9,repetition_penalty=1.2,
      max_new_tokens=100,pad_token_id=tokenizer.eos_token_id
  )
  inputs = tokenizer(prompt, return_tensors="pt").to('cuda')
  outputs = model.generate(**inputs, generation_config=generation_config)
  print("Outputs: ")
  print(outputs)
  theresponse = (tokenizer.decode(outputs[0], skip_special_tokens=True))
  print("The response: ")
  print(theresponse)
  return theresponse

def formatted_prompt(question)-> str:
    return f"<|im_start|>user\n{question}<|im_end|>\n<|im_start|>assistant:"

def parse_response(response):
  assistant_index = response.find('assistant:')
  answer = response[assistant_index + len('assistant:'):].strip()
  print('Answer: ')
  answer = answer.replace("<|im_start|>", "")
  answer = answer.replace("<|im_end|>", "")
  answer = answer.replace(".", "")
  answer = answer.replace(":", "")
  if "\n" in answer:
    answer = answer.split("\n")[0]
  answer = answer.replace("(", "").replace(")", "").replace(".", "").strip()
  print(answer)
  return answer

In [ ]:
import pandas as pd
testing = pd.read_csv('test_train_set (5).csv')

In [ ]:
instruction = "Complete the following sentence in one word without any explanation."
response_data = []
for index, row in tqdm(testing.iterrows()):
  ques = row["question"]
  #options = ast.literal_eval(row['options'])
  question = f'{instruction}\n{ques}\n'
  #for i, option in enumerate(options):
      #question += f'({i+1}) {option} '
  response = generate_response(user_input=question)
  row["response"] = response
  row["model_answer"] = parse_response(response)
  response_data.append(row)

1it [00:11, 11.46s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
          12833,    279,   2768,  11914,    304,    832,   3492,   2085,    904,
          16540,    627,   2746,  45509,   6439,    304,  14582,    337,  21781,
           3363,     11,   1243,  45509,   6439,    304,   6394,     27,     91,
            318,   6345,     91,    397,     27,     91,    318,   5011,     91,
             29,  78191,     25,   1614,    198,     27,     91,    318,   6345,
             91,   1822,     91,    318,   5011,     91,     29,   2513,    374,
            264,   1614,     13,  13853,     27,     91,    318,   6345,     91,
          16401,      0,  13853,   4235,     27,     91,    318,   5011,     91,
             29,   2513,    574,  14454,    505,    452,    408,   6347,   3224,
          16134,     91,    318,   6345,     91,   2511,  13853,   4235,     27,
             91,    318,   5011,     91,     29,     45,    408,   6347,   1614,
            706,  

2it [00:12,  5.38s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
          12833,    279,   2768,  11914,    304,    832,   3492,   2085,    904,
          16540,    627,   2746,  55769,   6439,    304,  76921,   1614,     11,
           1243,  55769,   6439,    304,   6394,     27,     91,    318,   6345,
             91,    397,     27,     91,    318,   5011,     91,     29,  78191,
             25,   3224,    627,     27,     91,    318,   6345,     91,     29,
         128001]], device='cuda:0')
The response: 
<|im_start|>user
Complete the following sentence in one word without any explanation.
If Nate lives in Vanguard state, then Nate lives in :
<|im_end|>
<|im_start|>assistant: country.
<|im_end|>
Answer: 
country


3it [00:23,  8.03s/it]

...

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
          12833,    279,   2768,  11914,    304,    832,   3492,   2085,    904,
          16540,    627,   2746,   7043,   6439,    304, 120815,     78,   3363,
             11,   1243,   7043,   6439,    304,   6394,     27,     91,    318,
           6345,     91,    397,     27,     91,    318,   5011,     91,     29,
          78191,     25,   1614,    198,     27,     91,    318,   6345,     91,
             29, 128001]], device='cuda:0')
The response: 
<|im_start|>user
Complete the following sentence in one word without any explanation.
If Paul lives in Tepo city, then Paul lives in :
<|im_end|>
<|im_start|>assistant: state
<|im_end|>
Answer: 
state


376it [26:36,  1.34s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
          12833,    279,   2768,  11914,    304,    832,   3492,   2085,    904,
          16540,    627,   2746,  14596,   6439,    304,   8409,   8458,   3363,
             11,   1243,  14596,   6439,    304,   6394,     27,     91,    318,
           6345,     91,    397,     27,     91,    318,   5011,     91,     29,
          78191,     25,   1614,   3224,    198,     27,     91,    318,   6345,
             91,     29, 128001]], device='cuda:0')
The response: 
<|im_start|>user
Complete the following sentence in one word without any explanation.
If Bob lives in Serela city, then Bob lives in :
<|im_end|>
<|im_start|>assistant: state country
<|im_end|>
Answer: 
state country


376it [26:38,  4.25s/it]


KeyboardInterrupt: 

In [ ]:
response_data_df = pd.DataFrame(response_data)
response_data_df.to_csv('response_training_set.csv')

## Synthetic data testing

In [ ]:
!pip install accelerate peft bitsandbytes transformers trl

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 122.4/122.4 MB 18.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 310.9/310.9 kB 24.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 36.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 16.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 13.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 17.4 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible

In [ ]:
import torch
from datasets import load_dataset, Dataset
from peft import LoraConfig, AutoPeftModelForCausalLM
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig, TrainingArguments
from trl import SFTTrainer
import os
from transformers import GenerationConfig
import pandas as pd
from tqdm import tqdm
import ast

In [ ]:
from huggingface_hub import notebook_login
notebook_login()


In [ ]:
model_id="Mona09/llama3.1-8B-Instruct-Fine-Reversal-Curse-2.0"


def get_model_and_tokenizer(model_id):
  tokenizer = AutoTokenizer.from_pretrained(model_id)
  tokenizer.pad_token = tokenizer.eos_token
  bnb_config = BitsAndBytesConfig(
      load_in_4bit=True, bnb_4bit_quant_type="nf4", bnb_4bit_compute_dtype="float16", bnb_4bit_use_double_quant=True
  )
  model = AutoModelForCausalLM.from_pretrained(
      model_id, quantization_config=bnb_config, device_map="auto"
  )
  model.config.use_cache=False
  model.config.pretraining_tp=1
  return model, tokenizer

# Load model
model, tokenizer = get_model_and_tokenizer(model_id)



/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/55.4k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.2M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/325 [00:00<?, ?B/s]

adapter_config.json:   0%|          | 0.00/662 [00:00<?, ?B/s]

...

model-00003-of-00004.safetensors:   0%|          | 0.00/4.92G [00:00<?, ?B/s]

model-00004-of-00004.safetensors:   0%|          | 0.00/1.17G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/184 [00:00<?, ?B/s]

adapter_model.safetensors:   0%|          | 0.00/13.6M [00:00<?, ?B/s]

#### Test Class 1

In [ ]:
def generate_response(user_input):
  prompt = formatted_prompt(user_input)
  inputs = tokenizer([prompt], return_tensors="pt")
  generation_config = GenerationConfig(penalty_alpha=0.6,do_sample = True,
      top_k=2,temperature=0.9,repetition_penalty=1.2,
      max_new_tokens=100,pad_token_id=tokenizer.eos_token_id
  )
  inputs = tokenizer(prompt, return_tensors="pt").to('cuda')
  outputs = model.generate(**inputs, generation_config=generation_config)
  print("Outputs: ")
  print(outputs)
  theresponse = (tokenizer.decode(outputs[0], skip_special_tokens=True))
  print("The response: ")
  print(theresponse)
  return theresponse

def formatted_prompt(question)-> str:
    return f"<|im_start|>user\n{question}<|im_end|>\n<|im_start|>assistant:"
    #return question

def parse_response(response):
  answer = response.split("<|im_start|>assistant:")[1].split("<|im_end|>")[0]
  print('Answer: ')
  print(answer)
  answer = answer.split()[-1]
  answer = answer.replace("<|im_start|>", "")
  answer = answer.replace("<|im_end|>", "")
  answer = answer.replace(".", "")
  answer = answer.replace(":", "")
  print(answer)
  if "\n" in answer:
    answer = answer.split("\n")[0]
  answer = answer.replace("(", "").replace(")", "").replace(".", "").strip()
  answer = answer.split(" ")[0]
  print(answer)
  #try:
    #answer = int(answer)
  #except:
    #answer = None
  return answer

In [ ]:
def calculate_accuracy(response_data):
  correct = 0
  total = 0

  for row in response_data:
    total += 1
    if row['model_answer'].lower() == row['gt_answer'].lower():
      correct += 1

  print(f"Correct: {correct}/{total}")
  print(f"Accuracy: {correct/total}")

def save_responses(response_data, path):
  response_data_df = pd.DataFrame(response_data)
  response_data_df.to_csv(path)

In [ ]:
#model, tokenizer = get_model_and_tokenizer('meta-llama/Meta-Llama-3.1-8B-Instruct')


In [ ]:
# load and read the testing csv
testing = pd.read_csv('final_synthetic_test_1.csv')
#instruction = "Select the number of the correct answer without any explanation. Do not answer with a sentence, just output the number of the correct option."


In [ ]:
# test on the dataset, save responses and get model answers
instruction = "Select the correct option and answer in one word without any explanation."
response_data = []
for index, row in tqdm(testing.iterrows()):
  ques = row["question"]
  options = ast.literal_eval(row['options'])
  question = f'{instruction}\n{ques}\n'
  for i, option in enumerate(options):
      question += f'({i+1}) {option} '
  response = generate_response(user_input=question)
  row["response"] = response
  row["model_answer"] = parse_response(response)
  response_data.append(row)



1it [00:03,  3.27s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,   1630,   7304,   1587,    539,
           3974,    304,    469,   5808,     11,   1243,   1630,   7304,   1587,
            539,   3974,    304,    512,      7,     16,      8,    386,  31866,
            320,     17,      8,  85214,   1636,     64,    320,     18,      8,
            735,   7897,  66652,    320,     19,      8,   1369,    441,    320,
             20,      8,  64898,   2629,    320,     21,      8,  20459,   6217,
          83739,    318,   6345,     91,    397,     27,     91,    318,   5011,
             91,     29,  78191,     25,     57,   1955,    320,     22,      8,
            650,  53413,    320,     23,      8,   9332,  15255,    320,     24,
              8,   1708,   1195,     64,    320,    605,      8,    350,   1147,
            258,  

2it [00:06,  3.51s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  98498,   1587,    539,   3974,
            304,   1630,     88,   1974,    689,     11,   1243,  98498,   1587,
            539,   3974,    304,    512,      7,     16,      8,    386,    974,
            320,     17,      8,   1443,   1082,    320,     18,      8,    426,
           5308,  38174,    320,     19,      8,  56534,  13637,    320,     20,
              8,  18024,   6217,    320,     21,      8,   1443,   6388,  83739,
            318,   6345,     91,    397,     27,     91,    318,   5011,     91,
             29,  78191,     25,   2059,    635,    320,     22,      8,    650,
           1247,     71,   5169,    366,     91,    318,   6345,     91,    397,
             40,   1781,    499,   8967,    311,   2019,    330,     53,  53413,
           3343,  

3it [00:10,  3.35s/it]

...

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  16768,   1587,    539,   3974,
            304,   8930,  87800,     11,   1243,  16768,   1587,    539,   3974,
            304,    512,      7,     16,      8,   2722,    441,    320,     17,
              8,  23683,    460,    320,     18,      8,    735,    731,    441,
            320,     19,      8,    423,   1394,    332,   5676,    320,     20,
              8,    350,    548,    320,     21,      8,    328,    437,    337,
            460,  83739,    318,   6345,     91,    397,     27,     91,    318,
           5011,     91,     29,  78191,     25,  38342,    460,  16134,     91,
            318,   6345,     91,     29, 128001]], device='cuda:0')
The response: 
<|im_start|>user
Select the correct option and answer in one word without any explanation.
If Kev

499it [12:01,  1.19s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  33305,   1587,    539,   3974,
            304,    469,   5808,     11,   1243,  33305,   1587,    539,   3974,
            304,    512,      7,     16,      8,    423,  19907,   8083,    320,
             17,      8,  22969,  40229,    320,     18,      8,  48869,    337,
          66652,    320,     19,      8,   1901,    359,    556,    320,     20,
              8,  48762,   2979,    320,     21,      8,    328,    974,     76,
          21781,  83739,    318,   6345,     91,    397,     27,     91,    318,
           5011,     91,     29,  78191,     25,     57,    587,  10649,  16134,
             91,    318,   6345,     91,     29, 128001]], device='cuda:0')
The response: 
<|im_start|>user
Select the correct option and answer in one word without any explanation

500it [12:02,  1.45s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  48390,   1587,    539,   3974,
            304,  11680,  61831,     11,   1243,  48390,   1587,    539,   3974,
            304,    512,      7,     16,      8,    650,  31478,    320,     17,
              8,  75571,    548,   6723,    320,     18,      8,  23683,    460,
            320,     19,      8,    452,    581,   5724,    320,     20,      8,
           1443,   6729,    320,     21,      8,    735,   6181,  83739,    318,
           6345,     91,    397,     27,     91,    318,   5011,     91,     29,
          78191,     25,     53,  31478,  32352,     91,    318,   6345,     91,
             29, 128009]], device='cuda:0')
The response: 
<|im_start|>user
Select the correct option and answer in one word without any explanation.
If Lily does not live in Lands

In [ ]:
calculate_accuracy(response_data)

save_responses(response_data, 'response_synthetic_test_1.csv')

Correct: 0/500
Accuracy: 0.0


In [ ]:
import ast

row = testing.head(2)
ques = row["question"].iloc[0]  # Access the value from the Series
options = ast.literal_eval(row['options'].iloc[0])  # Access the value from the Series
question = f'{instruction}\n{ques}\n'
for i, option in enumerate(options):
    question += f'({i+1}) {option} '
response = generate_response(user_input=question)
row["response"] = response
row["model_answer"] = parse_response(response)

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  89943,   6439,    304,    328,
           1295,  20218,     11,   1243,  89943,   6439,    304,    512,      7,
             16,      8,   7793,    263,     11,   1630,     88,   1974,    689,
            320,     17,      8,  15591,   4910,     11,  79763,   6347,    320,
             18,      8,  72313,    689,     11,   1676,  32106,    320,     19,
              8,    350,   1147,    258,     11,   1630,     88,   1974,    689,
            320,     20,      8,  11680,  61831,     11,   1901,    404,  66826,
            320,     21,      8,   7793,    263,     11,    469,   5808,  83739,
            318,   6345,     91,    397,     27,     91,    318,   5011,     91,
             29,  78191,     25,   2746,  89943,   6439,    304,    328,   1295,
          20218,  

<ipython-input-45-0f416d504b5d>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row["response"] = response
<ipython-input-45-0f416d504b5d>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row["model_answer"] = parse_response(response)


In [ ]:
print(row["model_answer"])

0    Almera
1    Almera
Name: model_answer, dtype: object


#### Test Class 2

In [ ]:
def parse_response(response):
  answer = response.split("<|im_start|>assistant:")[1].split("<|im_end|>")[0]
  print('Answer: ')
  print(answer)
  parts = answer.split(",")
  answer = ", ".join(part.strip() for part in parts[-2:])
  #answer = answer.split()[-1]
  answer = answer.replace("<|im_start|>", "")
  answer = answer.replace("<|im_end|>", "")
  answer = answer.replace(".", "")
  answer = answer.replace(":", "")
  print(answer)
  if "\n" in answer:
    answer = answer.split("\n")[0]
  answer = answer.replace("(", "").replace(")", "").replace(".", "").strip()
  #answer = answer.split(" ")[0]
  print(answer)
  #try:
    #answer = int(answer)
  #except:
    #answer = None
  return answer

In [ ]:
testing = pd.read_csv('final_synthetic_test_2.csv')

In [ ]:
import ast

row = testing.head(2)
ques = row["question"].iloc[0]  # Access the value from the Series
options = ast.literal_eval(row['options'].iloc[0])  # Access the value from the Series
question = f'{instruction}\n{ques}\n'
for i, option in enumerate(options):
    question += f'({i+1}) {option} '
response = generate_response(user_input=question)
row["response"] = response
row["model_answer"] = parse_response(response)

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  89943,   6439,    304,    328,
           1295,  20218,     11,   1243,  89943,   6439,    304,    512,      7,
             16,      8,   7793,    263,     11,   1630,     88,   1974,    689,
            320,     17,      8,  15591,   4910,     11,  79763,   6347,    320,
             18,      8,  72313,    689,     11,   1676,  32106,    320,     19,
              8,    350,   1147,    258,     11,   1630,     88,   1974,    689,
            320,     20,      8,  11680,  61831,     11,   1901,    404,  66826,
            320,     21,      8,   7793,    263,     11,    469,   5808,  83739,
            318,   6345,     91,    397,     27,     91,    318,   5011,     91,
             29,  78191,     25,  43057,  61831,     11,   1901,    404,    589,
            689,  

<ipython-input-55-0f416d504b5d>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row["response"] = response
<ipython-input-55-0f416d504b5d>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row["model_answer"] = parse_response(response)


In [ ]:
instruction = "Select the correct option and answer in one word without any explanation."
response_data = []
for index, row in tqdm(testing.iterrows()):
  ques = row["question"]
  options = ast.literal_eval(row['options'])
  question = f'{instruction}\n{ques}\n'
  for i, option in enumerate(options):
      question += f'({i+1}) {option} '
  response = generate_response(user_input=question)
  row["response"] = response
  row["model_answer"] = parse_response(response)
  response_data.append(row)

1it [00:02,  2.79s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  89943,   6439,    304,    328,
           1295,  20218,     11,   1243,  89943,   6439,    304,    512,      7,
             16,      8,   7793,    263,     11,   1630,     88,   1974,    689,
            320,     17,      8,  15591,   4910,     11,  79763,   6347,    320,
             18,      8,  72313,    689,     11,   1676,  32106,    320,     19,
              8,    350,   1147,    258,     11,   1630,     88,   1974,    689,
            320,     20,      8,  11680,  61831,     11,   1901,    404,  66826,
            320,     21,      8,   7793,    263,     11,    469,   5808,  83739,
            318,   6345,     91,    397,     27,     91,    318,   5011,     91,
             29,  78191,     25,   2746,  89943,   6439,    304,    328,   1295,
          20218,  

2it [00:04,  2.42s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  29335,   6439,    304,   1708,
           1195,     64,     11,   1243,  29335,   6439,    304,    512,      7,
             16,      8,    650,   1247,     71,  10649,     11,  79763,   6347,
            320,     17,      8,   8930,  87800,     11,    469,   5808,    320,
             18,      8,    426,  15697,    689,     11,   1901,    404,  66826,
            320,     19,      8,  37902,    277,    318,     11,   1630,     88,
           1974,    689,    320,     20,      8,   8930,  87800,     11,  79763,
           6347,    320,     21,      8,  37902,    277,    318,     11,   1676,
          32106,  83739,    318,   6345,     91,    397,     27,     91,    318,
           5011,     91,     29,  78191,     25,   1442,  42521,   6439,    304,
           1708,  

3it [00:06,  1.96s/it]

...

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  62253,   6439,    304,   1369,
          26738,     11,   1243,  62253,   6439,    304,    512,      7,     16,
              8,    480,   9451,    276,     11,   1630,     88,   1974,    689,
            320,     17,      8,   3400,  48121,     11,   1901,    404,  66826,
            320,     18,      8,   8930,  87800,     11,   1630,     88,   1974,
            689,    320,     19,      8,    426,  15697,    689,     11,    469,
           5808,    320,     20,      8,    735,    438,   5169,     11,   1676,
          32106,    320,     21,      8,   8930,  87800,     11,  79763,   6347,
          83739,    318,   6345,     91,    397,     27,     91,    318,   5011,
             91,     29,  78191,     25,   1442,  62253,   6439,    304,   1369,
          26738,  

499it [17:24,  1.76s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  98498,   6439,    304,    650,
           1003,  39476,     11,   1243,  98498,   6439,    304,    512,      7,
             16,      8,    452,    408,   6347,     11,   1901,    404,  66826,
            320,     17,      8,   1708,   1195,     64,     11,   1676,  32106,
            320,     18,      8,  11680,  61831,     11,  79763,   6347,    320,
             19,      8,  72313,    689,     11,   1901,    404,  66826,    320,
             20,      8,   7793,    263,     11, 123967,    411,    320,     21,
              8,  11680,  61831,     11,   1630,     88,   1974,    689,  83739,
            318,   6345,     91,    397,     27,     91,    318,   5011,     91,
             29,  78191,     25,  43057,  61831,     11,  79763,   6347,  16134,
             91,  

500it [17:26,  2.09s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  16768,   6439,    304,  15490,
             84,     11,   1243,  16768,   6439,    304,    512,      7,     16,
              8,  72313,    689,     11,    735,    438,   5169,    320,     17,
              8,    386,    556,   8350,     11,   1901,    301,    764,    277,
            320,     18,      8,    386,    556,   8350,     11,  83655,   9345,
            320,     19,      8,    452,    408,   6347,     11,    650,   1247,
             71,  10649,    320,     20,      8,  15591,   4910,     11,   3400,
          48121,    320,     21,      8,   7793,    263,     11,    480,   9451,
            276,  83739,    318,   6345,     91,    397,     27,     91,    318,
           5011,     91,     29,  78191,     25,   2746,  16768,   6439,    304,
          15490,  

In [ ]:
calculate_accuracy(response_data)

save_responses(response_data, 'response_synthetic_test_2.csv')

#### Test Class 4

In [ ]:
def parse_response(response):
  answer = response.split("<|im_start|>assistant:")[1].split("<|im_end|>")[0]
  print('Answer: ')
  print(answer)
  answer = answer.split()[-1]
  answer = answer.replace("<|im_start|>", "")
  answer = answer.replace("<|im_end|>", "")
  answer = answer.replace(".", "")
  answer = answer.replace(":", "")
  print(answer)
  if "\n" in answer:
    answer = answer.split("\n")[0]
  answer = answer.replace("(", "").replace(")", "").replace(".", "").strip()
  answer = answer.split(" ")[0]
  print(answer)
  #try:
    #answer = int(answer)
  #except:
    #answer = None
  return answer

In [ ]:
testing = pd.read_csv('final_synthetic_test_4.csv')

In [ ]:
instruction = "Select the correct option and answer in one word without any explanation."
response_data = []
for index, row in tqdm(testing.iterrows()):
  ques = row["question"]
  options = ast.literal_eval(row['options'])
  question = f'{instruction}\n{ques}\n'
  for i, option in enumerate(options):
      question += f'({i+1}) {option} '
  response = generate_response(user_input=question)
  row["response"] = response
  row["model_answer"] = parse_response(response)
  response_data.append(row)

1it [00:02,  2.57s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  64787,   6439,    304,  11824,
           6388,    477,  18165,    575,   1295,     11,   1243,  64787,   6439,
            304,    512,      7,     16,      8,    426,  15697,    689,    320,
             17,      8,    650,   1247,     71,  10649,    320,     18,      8,
          11119,    376,    689,    320,     19,      8,  83655,   9345,    320,
             20,      8,   1901,    301,    764,    277,    320,     21,      8,
          37902,    277,    318,  83739,    318,   6345,     91,    397,     27,
             91,    318,   5011,     91,     29,  78191,     25,   1442,  64787,
           6439,    304,  11824,   6388,    477,  18165,    575,   1295,     11,
           1243,  64787,   6439,    304,    350,    438,   5169,  16134,     91,
            318,  

2it [00:03,  1.77s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  40394,   6439,    304,   1443,
            635,    477,    328,   4385,  15782,     11,   1243,  40394,   6439,
            304,    512,      7,     16,      8,   3400,  48121,    320,     17,
              8,    426,  15697,    689,    320,     18,      8,   1901,    301,
            764,    277,    320,     19,      8,    480,   9451,    276,    320,
             20,      8,  11119,    376,    689,    320,     21,      8,  83655,
           9345,  83739,    318,   6345,     91,    397,     27,     91,    318,
           5011,     91,     29,  78191,     25,     57,    301,    764,    277,
          16134,     91,    318,   6345,     91,     29, 128009]],
       device='cuda:0')
The response: 
<|im_start|>user
Select the correct option and answer in one word without 

3it [00:06,  2.11s/it]

...

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  45509,   6439,    304,   2418,
            344,    460,    477,  23971,    288,  53413,     11,   1243,  45509,
           6439,    304,    512,      7,     16,      8,  72313,    689,    320,
             17,      8,   7793,    263,    320,     18,      8,  76921,    320,
             19,      8,    386,    556,   8350,    320,     20,      8,    452,
            408,   6347,    320,     21,      8,    350,   1147,    258,  83739,
            318,   6345,     91,    397,     27,     91,    318,   5011,     91,
             29,  78191,     25,     18,  27530,     91,    318,   6345,     91,
            397,     27,     91,    318,   5011,     91,     29,   2746,  45509,
           6439,    304,   2418,    344,    988,   4657,     11,   1243,  45509,
           6439,  

499it [13:21,  2.10s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  40394,   6439,    304,    328,
           6868,    477,   1050,     89,    664,    460,     11,   1243,  40394,
           6439,    304,    512,      7,     16,      8,    386,    556,   8350,
            320,     17,      8,   1708,   1195,     64,    320,     18,      8,
          15591,   4910,    320,     19,      8,   9332,  15255,    320,     20,
              8,  72313,    689,    320,     21,      8,    452,    408,   6347,
          83739,    318,   6345,     91,    397,     27,     91,    318,   5011,
             91,     29,  78191,     25,   2746,  40394,   6439,    304,    328,
           6868,    477,   1050,     89,    664,    460,     11,   1243,  40394,
           6439,    304,  15591,   4910,  16134,     91,    318,   6345,     91,
             29, 1

500it [13:22,  1.61s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  40394,   6439,    304,    735,
            752,    316,   3105,    477,  33621,   2979,     11,   1243,  40394,
           6439,    304,    512,      7,     16,      8,    350,   1147,    258,
            320,     17,      8,   7793,    263,    320,     18,      8,  15591,
           4910,    320,     19,      8,    452,    408,   6347,    320,     20,
              8,  72313,    689,    320,     21,      8,   1708,   1195,     64,
          83739,    318,   6345,     91,    397,     27,     91,    318,   5011,
             91,     29,  78191,     25,   2803,    263,  16134,     91,    318,
          11137,     91,     29, 128009]], device='cuda:0')
The response: 
<|im_start|>user
Select the correct option and answer in one word without any explanation.
If Julia lives

In [ ]:
calculate_accuracy(response_data)

save_responses(response_data, 'response_synthetic_test_4.csv')

Correct: 0/500
Accuracy: 0.0


#### Test Class 5

In [ ]:
testing = pd.read_csv('final_synthetic_test_5.csv')

In [ ]:
instruction = "Select the correct option and answer in one word without any explanation."
response_data = []
for index, row in tqdm(testing.iterrows()):
  ques = row["question"]
  options = ast.literal_eval(row['options'])
  question = f'{instruction}\n{ques}\n'
  for i, option in enumerate(options):
      question += f'({i+1}) {option} '
  response = generate_response(user_input=question)
  row["response"] = response
  row["model_answer"] = parse_response(response)
  response_data.append(row)

1it [00:01,  1.20s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  68200,   6439,    304,   1708,
           1195,     64,     11,    480,   9451,    276,     11,   1243,  68200,
           6439,    304,    512,      7,     16,      8,  79763,   6347,    320,
             17,      8,    469,   5808,    320,     18,      8,   1676,  32106,
            320,     19,      8,   1901,    404,  66826,    320,     20,      8,
         123967,    411,    320,     21,      8,   1630,     88,   1974,    689,
          83739,    318,   6345,     91,    397,     27,     91,    318,   5011,
             91,     29,  78191,     25,     57,    404,  66826,  16134,     91,
            318,   6345,     91,     29, 128001]], device='cuda:0')
The response: 
<|im_start|>user
Select the correct option and answer in one word without any explanation.
If Ver

2it [00:02,  1.20s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  68200,   6439,    304,    328,
          32945,     11,   7793,    263,     11,   1243,  68200,   6439,    304,
            512,      7,     16,      8,   1676,  32106,    320,     17,      8,
            469,   5808,    320,     18,      8, 123967,    411,    320,     19,
              8,   1901,    404,  66826,    320,     20,      8,   1630,     88,
           1974,    689,    320,     21,      8,  79763,   6347,  83739,    318,
           6345,     91,    397,     27,     91,    318,   5011,     91,     29,
          78191,     25,     57,    404,    589,    521,  16134,     91,    318,
           6345,     91,     29, 128001]], device='cuda:0')
The response: 
<|im_start|>user
Select the correct option and answer in one word without any explanation.
If Vera lives 

3it [00:03,  1.17s/it]

...

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  31797,   6439,    304,    445,
            548,     11,   7793,    263,     11,   1243,  31797,   6439,    304,
            512,      7,     16,      8,    426,  15697,    689,    320,     17,
              8,    650,   1247,     71,  10649,    320,     18,      8,  11119,
            376,    689,    320,     19,      8,   8930,  87800,    320,     20,
              8,  83655,   9345,    320,     21,      8,    480,   9451,    276,
          83739,    318,   6345,     91,    397,     27,     91,    318,   5011,
             91,     29,  78191,     25,     53,   1247,     71,  10649,  16134,
             91,    318,   6345,     91,     29, 128009]], device='cuda:0')
The response: 
<|im_start|>user
Select the correct option and answer in one word without any explanation

499it [13:54,  3.78s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  63264,   6439,    304,    423,
           6181,     11,  72313,    689,     11,   1243,  63264,   6439,    304,
            512,      7,     16,      8,    426,  15697,    689,    320,     17,
              8,   8930,  87800,    320,     18,      8,   1901,    301,    764,
            277,    320,     19,      8,  37902,    277,    318,    320,     20,
              8,    650,   1247,     71,  10649,    320,     21,      8,    480,
           9451,    276,  83739,    318,   6345,     91,    397,     27,     91,
            318,   5011,     91,     29,  78191,     25,   1442,   5496,    304,
            423,   6181,     11,   1243,   5496,    304,    350,   1147,    258,
          16134,     91,    318,   6345,     91,    397,     27,     91,    318,
           5011,  

500it [13:55,  1.67s/it]

Outputs: 
tensor([[128000,     27,     91,    318,   5011,     91,     29,    882,    198,
           3461,    279,   4495,   3072,    323,   4320,    304,    832,   3492,
           2085,    904,  16540,    627,   2746,  14596,   6439,    304,  23109,
           2548,     72,     11,  76921,     11,   1243,  14596,   6439,    304,
            512,      7,     16,      8,    650,   1247,     71,  10649,    320,
             17,      8,   8930,  87800,    320,     18,      8,  37902,    277,
            318,    320,     19,      8,    426,  15697,    689,    320,     20,
              8,  83655,   9345,    320,     21,      8,   3400,  48121,  83739,
            318,   6345,     91,    397,     27,     91,    318,   5011,     91,
             29,  78191,     25,  27814,  87800,  16134,     91,    318,   6345,
             91,     29, 128009]], device='cuda:0')
The response: 
<|im_start|>user
Select the correct option and answer in one word without any explanation.
If Bob lives in Karesh

In [ ]:
calculate_accuracy(response_data)

save_responses(response_data, 'response_synthetic_test_5.csv')

Correct: 0/500
Accuracy: 0.0


### Evaluations:



In [ ]:
import pandas as pd

file_path = 'response_synthetic_test_1.csv'
data = pd.read_csv(file_path)

import string

def compare_strings_ignore_case_punctuation(str1, str2):
    translator = str.maketrans('', '', string.punctuation)
    clean_str1 = str1.translate(translator).lower()
    clean_str2 = str2.translate(translator).lower()
    return clean_str1 == clean_str2

data['correct'] = data.apply(lambda row: compare_strings_ignore_case_punctuation(row['gt_answer'], row['model_answer']), axis=1)

accuracy = data['correct'].mean()


print(accuracy)
data.to_csv('evaluation_synthetic_test_1.csv')

0.11


In [ ]:
import pandas as pd
import string

file_path = 'response_synthetic_test_2.csv'
data = pd.read_csv(file_path)

def all_words_in_model(gt_answer, model_answer):
    translator = str.maketrans('', '', string.punctuation)
    gt_words = gt_answer.translate(translator).lower().split()
    model_words = model_answer.translate(translator).lower().split()
    return all(word in model_words for word in gt_words)

data['correct'] = data.apply(lambda row: all_words_in_model(str(row['gt_answer']), str(row['model_answer'])), axis=1)

accuracy = data['correct'].mean()


print(accuracy)

data.to_csv('evaluation_synthetic_test_2.csv')

0.054


In [ ]:
import pandas as pd

file_path = 'response_synthetic_test_4.csv'
data = pd.read_csv(file_path)

import string

def compare_strings_ignore_case_punctuation(str1, str2):
    translator = str.maketrans('', '', string.punctuation)
    clean_str1 = str1.translate(translator).lower()
    clean_str2 = str2.translate(translator).lower()
    return clean_str1 == clean_str2

data['correct'] = data.apply(lambda row: compare_strings_ignore_case_punctuation(row['gt_answer'], row['model_answer']), axis=1)

accuracy = data['correct'].mean()


print(accuracy)
data.to_csv('evaluation_synthetic_test_4.csv')

0.114


In [ ]:
import pandas as pd

file_path = 'response_synthetic_test_5.csv'
data = pd.read_csv(file_path)

import string

def compare_strings_ignore_case_punctuation(str1, str2):
    translator = str.maketrans('', '', string.punctuation)
    clean_str1 = str1.translate(translator).lower()
    clean_str2 = str2.translate(translator).lower()
    return clean_str1 == clean_str2

data['correct'] = data.apply(lambda row: compare_strings_ignore_case_punctuation(row['gt_answer'], row['model_answer']), axis=1)

accuracy = data['correct'].mean()


print(accuracy)
data.to_csv('evaluation_synthetic_test_5.csv')

0.078
